<a href="https://colab.research.google.com/github/Heba2424/Arabic-Book-Summary-Generator/blob/main/Copy_of_Generate_Summery.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Install Necessary Libraries

In [ ]:
# Install specific compatible versions of necessary libraries
!pip uninstall -y pyarrow --quiet
!pip install pyarrow==14.0.1 torch transformers datasets

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

In [ ]:
!pip install gradio --quiet

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.4/50.4 kB 4.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.4/12.4 MB 108.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.2/318.2 kB 28.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 141.1/141.1 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 72.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.8/62.8 kB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.2/92.2 kB 9.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.9/71.9 kB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 13.0 MB/s eta 0:00:00
   ━━━━━━

## Import Libraries and Define Data

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

df = pd.read_csv('/content/summery (1).csv')
df.head()

Summaries
0  كتاب المبادئ الأساسية لفهم القرآن الكريم PDF ت...
1  كتاب الحجاب PDF تلخيص كتاب الحجاب PDF للكاتب أ...
2  كتاب الخلافة والملك PDF تلخيص كتاب الخلافة وال...
3  كتاب مبادئ الإسلام PDF تلخيص كتاب مبادئ الإسلا...
4  كتاب المصطلحات الأربعة في القرآن PDF تلخيص كتا...

## Define Clean Text Function and Clean Summaries

In [ ]:
import pandas as pd
import re
from transformers import AutoTokenizer, GPT2LMHeadModel, Trainer, TrainingArguments
import torch
from torch.utils.data import Dataset, DataLoader


# Define the clean_text function for Arabic text
def clean_text(text):
    if not isinstance(text, str):
        return ""
    text = re.sub(r'<[^>]+>', '', text)  # Remove HTML tags
    text = re.sub(r'\s+', ' ', text)  # Replace multiple spaces with a single space
    text = re.sub(r'[^\w\s,.?!ءاأإآئؤن]', '', text)  # Remove special characters (keeping Arabic characters and common punctuation)
    text = text.strip()
    return text

# Apply clean_text to each summary in the DataFrame
cleaned_summaries = [clean_text(summary) for summary in df['Summaries']]

# Filter out empty summaries
cleaned_summaries = [summary for summary in cleaned_summaries if summary.strip() != ""]

# Print cleaned summaries to verify
cleaned_summaries


['كتاب المبادئ الأساسية لفهم القرآن الكريم PDF تلخيص كتاب المبادئ الأساسية لفهم القرآن الكريم PDF للكاتب أبو الأعلى المودودي يعد كتاب المبادئ الأساسية لفهم القرآن الكريم PDF أحد أبرز أعمال الكاتب المشهور أبو الأعلى المودودي فقد غطت أعماله مجموعة من التخصصات مثل تفسير القرآن والحديث والقانون والفلسفة والتاريخ تمت كتابتها باللغة الأردية ولكن بعد ذلك ترجمت إلى الإنجليزية والعربية والعديد من اللغات الأخرى فلاقى هذا الكتاب شهرة وقبول واسع في قلوب المسلمين في شتى البقاع. يساعد كتاب المبادئ الأساسية لفهم القرآن الكريم PDF على فهم التنوع والغنى الذي يتميز به القرآن. يتناول الكتاب مواضيع العقائد والأخلاق والشريعة والدعوة والنصح والتخويف والترغيب والحجج والشواهد والقصص التاريخية والإشارات إلى آيات الله في الكون كل ذلك بأسلوب يجمع بين التعمق الفكري والوضوح التوضيحي. كتاب المبادئ الأساسية لفهم القرآن الكريم PDF نبذة عن الكاتب أبو الأعلى المودودي الكاتب أبو الأعلى المودودي هو عالم ومنظر إسلامي إسلاميا وفيلسوف مسلم وفقيه ومؤرخ وصحفي وناشط فقد سعى إلى إحياء الإسلام كمنهج حياة شامل حيث وصف بأنه أكثر ا

## Tokenize Summaries

In [ ]:
# Load a pre-trained tokenizer for Arabic
tokenizer = AutoTokenizer.from_pretrained('aubmindlab/aragpt2-medium')
tokenizer.add_special_tokens({'pad_token': '[PAD]'})

# Tokenize the summaries
def tokenize_function(summary):
    return tokenizer(summary, truncation=True, padding='max_length', max_length=512)

tokenized_summaries = [tokenize_function(summary) for summary in cleaned_summaries]


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:99: UserWarning: 
Error while fetching `HF_TOKEN` secret value from your vault: 'Requesting secret HF_TOKEN timed out. Secrets can only be fetched when running from the Colab UI.'.
You are not authenticated with the Hugging Face Hub in this notebook.
If the error persists, please let us know by opening an issue on GitHub (https://github.com/huggingface/huggingface_hub/issues/new).
  warnings.warn(


config.json:   0%|          | 0.00/843 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.94M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.50M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/4.52M [00:00<?, ?B/s]

## Create Dataset

In [ ]:
# Define a custom dataset
class SummaryDataset(Dataset):
    def __init__(self, tokenized_summaries):
        self.tokenized_summaries = tokenized_summaries

    def __len__(self):
        return len(self.tokenized_summaries)

    def __getitem__(self, idx):
        return {'input_ids': torch.tensor(self.tokenized_summaries[idx]['input_ids'], dtype=torch.long),
                'attention_mask': torch.tensor(self.tokenized_summaries[idx]['attention_mask'], dtype=torch.long),
                'labels': torch.tensor(self.tokenized_summaries[idx]['input_ids'], dtype=torch.long)}

# Create the dataset
dataset = SummaryDataset(tokenized_summaries)


## Load Model and Define Trainer

In [ ]:
# Load a pre-trained model
model = GPT2LMHeadModel.from_pretrained('aubmindlab/aragpt2-medium')
model.resize_token_embeddings(len(tokenizer))

# Define training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
)

# Create a Trainer instance
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=dataset
)


model.safetensors:   0%|          | 0.00/1.50G [00:00<?, ?B/s]

## Train the Model

In [ ]:
# Train the model
trainer.train()


TrainOutput(global_step=3540, training_loss=1.3889065322229417, metrics={'train_runtime': 6901.4732, 'train_samples_per_second': 2.051, 'train_steps_per_second': 0.513, 'total_flos': 1.3144829630349312e+16, 'train_loss': 1.3889065322229417, 'epoch': 3.0})

In [ ]:
!mv /content/results /content/drive/MyDrive/Generate_Summery

mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-2500/optimizer.pt': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-2500/scheduler.pt': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-2500/rng_state.pth': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-2500/trainer_state.json': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-3540/config.json': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-3540/generation_config.json': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-3540/model.safetensors': No space left on device
mv: error writing '/content/drive/MyDrive/Generate_Summery/results/checkpoint-3540/training_args.bin': No space left on devic

In [ ]:
!mv /content/logs /content/drive/MyDrive/Generate_Summery

mv: cannot stat '/content/logs': No such file or directory


## Define Summary Generation Function

In [ ]:
# Define the function to generate summaries for any book in Arabic
def generate_summary_for_any_book(book_description, model, tokenizer, max_length=512):
    model.eval()
    inputs = tokenizer.encode(book_description, return_tensors='pt').to(model.device)
    outputs = model.generate(inputs, max_length=max_length, num_return_sequences=1, no_repeat_ngram_size=2)
    summary = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return summary

# Example usage
new_book_description = "قصة ساحر شاب يكتشف إرثه السحري ويحضر مدرسة للسحر."
generated_summary = generate_summary_for_any_book(new_book_description, model, tokenizer)
print(generated_summary)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token.As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


قصة ساحر شاب يكتشف إرثه السحري ويحضر مدرسة للسحر. وهذا ملخص قصة ساحر فتى يكتشف رفقا كبيرا في مدرسة السحر. نبذة عن كاتب قصة الساحر فتى يبلغ من العمر اثني عشر عاما فقط. ولد في قرية صغيره في محافظة الدقهلية. عاش مع جدته في القرية بعد وفاة والده. بدأ رحلته في البحث عن والده الذي كان يعمل في صناعة تقطير ماء الورد. وبعد ذلك بدأ في جمع الأموال اللازمة للزواج من عمه الذي لم يستجب لطلب والده بإعفائه من العمل. ومع مرور الوقت يكتشف أن والده قد مات بالفعل. في نهاية القصة يكتشف الساحر أن جده قد سرق مبلغ ستة جنيهات من جار له في إحدى القرى. وفي نهاية الأحداث يكتشف الشاب أن جده قد توفي بالفعل وأن والده كان يعلم بأمر هذا الرجل. فهل سيتمكن من كشف الحقيقة وكشف الحقيقة أم أن هناك سر وراء اختفاء مبلغ الستة جنيهات. اقرأ القصة وانضم إلى فريق القصة. محتويات قصة كتاب ساحر فتاة يكتشف إهاما فتاة صغيرة تعيش في عزلة تامة مع والدها. بعد ذلك يكتشف أنها تعيش حياة صعبة. تكتشف إيما أنها تعاني من معاملة سيئة من زوجة والدها بسبب معاملتها السيئة تجاهها. تتطور الأحداث بسرعة عندما تكتشف أن والدها قد توفيت بالفعل وأنها تعيش 

## Deploy with Gradio

In [ ]:
import gradio as gr

def gradio_generate_summary(book_description):
    return generate_summary_for_any_book(book_description, model, tokenizer)

# Create a Gradio interface
interface = gr.Interface(
    fn=gradio_generate_summary,
    inputs=gr.Textbox(lines=2, placeholder="Enter book description here..."),
    outputs="text",
    title="Arabic Book Summary Generator",
    description="Enter a book description in Arabic and get a generated summary."
)

# Launch the Gradio interface
interface.launch(share=True)



Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://b6cf3ec2b5441abb8e.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
